<div style="font-size:30px" align="center"> <b> Using Node Embeddings to Study Open Source Software Collaborations </b> </div>

<div style="font-size:18px" align="center"> <b> Brandon Kramer, UVA Biocomplexity Institute, OSS DSPG 2021 </b> </div>

<br>

### Setup  

In this notebook, we use `node2vec` to study open source software collaborations. First, let's load all of our modules and our node and edge data from the PostgreSQL database.

In [1]:
%matplotlib inline

# load modules 
import warnings
from datetime import datetime
from text_unidecode import unidecode
from collections import deque
import os
import multiprocessing
import psycopg2 as pg
import pandas.io.sql as psql
import pandas as pd
from sklearn.manifold import TSNE
import numpy as np
import networkx as nx
from gensim.models import Word2Vec
from node2vec import Node2Vec
import altair as alt
warnings.filterwarnings('ignore')

# connect to the database, download data 
connection = pg.connect(host = 'postgis1', database = 'sdad', 
                        user = os.environ.get('db_user'), 
                        password = os.environ.get('db_pwd'))

edgelist_data = '''SELECT ctr1, ctr2, repo_wts as weight 
                   FROM gh_sna.sna_intl_ctr_edgelist_0819 by LIMIT 50000'''
nodelist_data = '''select * from gh.sna_ctr_sectors '''

# convert to a dataframe, show how many missing we have (none)
edgelist_data = pd.read_sql_query(edgelist_data, con=connection)
nodelist_data = pd.read_sql_query(nodelist_data, con=connection)

# convert the edgelist to a graph 
graph = nx.from_pandas_edgelist(edgelist_data, source='ctr1', target='ctr2', edge_attr='weight')

print("Node count:", graph.number_of_nodes(), "- Edge count:", graph.number_of_edges())

Node count: 2830 - Edge count: 50000


### Training node2vec

Next, we use `node2vec` to embed the network subset and save the model for later visualization.

In [37]:
cores_available = multiprocessing.cpu_count() - 1

# train the graph with node2vec 
print("Started at:", datetime.now())
# node2vec
node2vec = Node2Vec(graph, dimensions=20, walk_length=16, num_walks=100, workers=cores_available)
# extract model
model = node2vec.fit(window=10, min_count=1)
print("Finished at:", datetime.now())

os.chdir('/project/biocomplexity/sdad/projects_data/ncses/oss/dspg_2021/')
model.save("node2vec_test.model")

# Running large graphs 
# https://github.com/eliorc/node2vec
# https://github.com/eliorc/node2vec/blob/master/example.py
#node2vec = Node2Vec(graph, dimensions=64, walk_length=30, num_walks=200, workers=4, temp_folder="/mnt/tmp_data")

Started at: 2021-07-18 09:36:02.289858


Computing transition probabilities:   0%|          | 0/2830 [00:00<?, ?it/s]

Finished at: 2021-07-18 09:38:37.756443


### Incorporating Node Attributes

Once we have the node embedding data (in a multidimensional space), we can make some interesting visualizations. Before we do that, we are going to run some basic network centrality measures (degree centrality, betweenness centrality, and page rank) to supplment our visualizations. Second, we will need to reduce the dimensions of the node embeddings by using t-distributed stochastic neighbor embedding (`TSNE` from `scikit-learn`). Lastly, we are going to join our node attributes (companies, countries and sectors) to help our final analyses.  

In [2]:
# import the node2vec model 
os.chdir('/project/biocomplexity/sdad/projects_data/ncses/oss/dspg_2021/')
model = Word2Vec.load("node2vec_test.model")

# run centrality measures 
deg_cent = nx.degree_centrality(graph)
btw_cent = nx.betweenness_centrality(graph, normalized = True, endpoints = False)
page_rank = nx.pagerank(graph, alpha = 0.8)
deg_cent_df = pd.DataFrame(deg_cent.items(), columns=['login', 'deg_cent'])
btw_cent_df = pd.DataFrame(btw_cent.items(), columns=['login', 'btw_cent'])
page_rank_df = pd.DataFrame(page_rank.items(), columns=['login', 'page_rank'])
deg_cent_df = btw_cent_df.join(deg_cent_df.set_index('login'), on='login', how='left')
cent_measures = page_rank_df.join(deg_cent_df.set_index('login'), on='login', how='left')
cent_measures

# join all of the node attributes together for data viz 
vocab = list(model.wv.vocab)
model_x = model[vocab]
model_tsne = TSNE(n_components=2)
model_tsne_x = model_tsne.fit_transform(model_x)
model_tsne_x
tsne_df = pd.DataFrame(model_tsne_x, index=vocab, columns=['x', 'y'])
tsne_df["login"] = vocab
tsne_df = tsne_df.join(nodelist_data.set_index('login'), on='login', how='left')
tsne_df = cent_measures.join(tsne_df.set_index('login'), on='login', how='left')
tsne_df

login  page_rank      btw_cent  deg_cent          x          y  \
0        jstrachan   0.000569  3.749807e-07  0.001767  -1.687289   7.943987   
1        rawlingsj   0.000515  3.749807e-07  0.001767  -1.687762   7.944228   
2     hectorsector   0.000660  1.416594e-06  0.001767 -11.379122  11.509637   
3      hollenberry   0.000487  1.666581e-07  0.001414 -11.380832  11.512714   
4          crichID   0.000489  0.000000e+00  0.001060 -11.380404  11.510748   
...            ...        ...           ...       ...        ...        ...   
2825  venilnoronha   0.000091  0.000000e+00  0.000707  32.339172  24.015085   
2826      kulikala   0.000194  0.000000e+00  0.008484 -38.913094 -20.007263   
2827      rriemann   0.000195  0.000000e+00  0.001060  44.269444   8.796278   
2828        ebassi   0.000086  0.000000e+00  0.000353   0.664299  -5.848925   
2829  EricLuehrsen   0.000076  0.000000e+00  0.000353  17.984329   0.544497   

            sector  city_info cc_multiple   cc_di cc_viz  \
0         business       None          gb  single     gb   
1         business    cardiff          gb  single     gb   
2     null/missing    orlando          us  single     us   
3         business  san diego          us  single     us   
4         business       None          us  single     us   
...            ...        ...         ...     ...    ...   
2825      business  palo alto          us  single     us   
2826  null/missing      tokyo          jp  single     jp   
2827  null/missing       lyon          fr  single     fr   
2828  null/missing     london          gb  single     gb   
2829  null/missing       None          us  single     us   

                raw_location                     email company_original  \
0                  Mells, UK  james.strachan@gmail.com        CloudBees   
1                    Cardiff     rawlingsj80@gmail.com        CloudBees   
2                Orlando, FL                      None             None   
3             San Diego, CA                       None           GitHub   
4                         NC                      None           GitHub   
...                      ...                       ...              ...   
2825   Palo Alto, California     hello@venilnoronha.io          @vmware   
2826             Tokyo/Japan                      None             None   
2827                    Lyon         robert@riemann.cc             None   
2828              London, UK          ebassi@gmail.com             None   
2829  Dearborn, Michigan, US    ericluehrsen@gmail.com             None   

     company_cleaned  
0          cloudbees  
1          cloudbees  
2               None  
3             github  
4             github  
...              ...  
2825          vmware  
2826            None  
2827            None  
2828            None  
2829            None  

[2830 rows x 15 columns]

### Node Embedding Visualizations 

First, we can visualize these embeddings by sector. Given that most the nodes are from the 

In [3]:
domain = ['academic', 'business', 'non-profit', 'government']# , 'not classified', 'null/missing']
range_ = ['crimson', 'teal', 'darkorange', 'darkblue'] #, 'lightgrey', 'lightgrey']

alt.Chart(tsne_df,title="Node Embedding of OSS Collaboration Networks (by Sector)").mark_circle().encode(
   x='x', y='y', 
    color=alt.Color('sector', scale=alt.Scale(domain=domain, range=range_)),
    size=alt.Size('page_rank'),
    tooltip=['login', 'sector', 'city_info', 'cc_viz', 'company_original', 'company_cleaned']
).interactive().properties(
    width=700,
    height=500
)

alt.Chart(...)

In [10]:
domain = ['microsoft', 'google', 'red hat', 'ibm', 'facebook', 'intel', 'thoughtworks', 'alibaba', 'amazon', 'databricks']

alt.Chart(tsne_df, title="Node Embedding of OSS Collaboration Networks (Top Companies)").mark_circle().encode(
   x='x', y='y', 
    color=alt.Color('company_cleaned', scale=alt.Scale(domain=domain)),
    size=alt.Size('page_rank'),
    tooltip=['login', 'sector', 'city_info', 'cc_viz', 'company_original', 'company_cleaned']
).interactive().properties(
    width=700,
    height=500
)

alt.Chart(...)

In [58]:
alt.Chart(tsne_df, title="Node Embedding of OSS Collaboration Networks (by Company)").mark_circle(size=150).encode(
   x='x', y='y', 
    color='company_cleaned',#alt.Color('sector', scale=alt.Scale(domain=domain, range=range_)),
    size=alt.Size('page_rank'),
    tooltip=['login', 'sector', 'city_info', 'cc_viz', 'company_original', 'company_cleaned']
).interactive().properties(
    width=700,
    height=500
)

alt.Chart(...)

In [59]:
alt.Chart(tsne_df,title="Node Embedding of OSS Collaboration Networks (by Country)").mark_circle(size=150).encode(
   x='x', y='y', 
    color='cc_viz',
    size=alt.Size('page_rank'),
    tooltip=['login', 'sector', 'city_info', 'cc_viz', 'company_original', 'company_cleaned']
).interactive().properties(
    width=700,
    height=500
)

alt.Chart(...)

In [4]:
for node, _ in model.most_similar('rasbt'):
    # Show only players
    if len(node) > 3:
        print(node)

buaaliyi
rinugun
yuanbyu
EronWright
charlesnicholson
sugyan
darrengarvey
markmcd
zafartahirov
vahidk


### Future directions

https://github.com/shenweichen/GraphEmbedding <<< 

node2vec 
struc2vec

[Node2Vec Tutorial](https://github.com/eliorc/Medium/blob/master/Nod2Vec-FIFA17-Example.ipynb)
